In [1]:
import json
import pandas as pd
import numpy as np
import folium

The raw data is a list of disconnected points (with certain GeoJSON keys, aka 'features', that relate them to a train line/track).  
We want to extract a list of lines from this data.

In [2]:
data = json.load(open('/home/germain/Documents/uni/EPFL/Data Vis/Project/ignore/courbe-des-voies.geojson'))

First, we group the points by train line/track while retaining all the GeoJSON features:

In [3]:
lines_by_features = {}
for feature in data['features']:
    # Get a unique key that identifies each line and track.
    key = '{},{},{},{}'.format(feature['properties']['nom_voie'], feature['properties']['code_ligne'],
                               feature['properties']['libelle_voie'], feature['properties']['libelle_ligne'])
    if key in lines_by_features:
        lines_by_features[key].append(feature)
    else:
        lines_by_features[key] = [feature]

Then, for each line/track's points, we only keep the point's code ("pk_debut" -- primary key?) and coordinates. We will then sort the points by their code, which gives us the ordered points of each line/track.

In [5]:
lines_by_points = []
for key, line in lines_by_features.items():
    points = {}
    for feature in line:
        if feature['geometry']:
            coord = feature['geometry']['coordinates']
            start_code = feature['properties']['pk_debut']
            # For correct sorting, we want all numbers to have the same length (e.g. "97+123" should be
            # "097+123", so that "097+123" < "100+345").
            start_code_split = start_code.split('+') if '+' in start_code else start_code.split('-')
            start_code = '{:03}+{:03}'.format(int(start_code_split[0]), int(start_code_split[1]))
            points[start_code] = coord
    lines_by_points.append({'name': key, 'points': points})

In [6]:
# Sort by starting code.
for i in range(len(lines_by_points)):
    lines_by_points[i]['points'] = dict(sorted(lines_by_points[i]['points'].items()))

Now that we have the ordered points for each line/track, we simply build a geometrical line by connecting them. We also add some additional GeoJSON properties that will be shown as tooltips, so we can debug/visualize things better on the Folium map.

In [7]:
lines_geojson_features = []
for line_by_points in lines_by_points:
    line = []
    for start_code, coord in line_by_points['points'].items():
        line.append(coord)
    name = line_by_points['name'].split(',')
    lines_geojson_features.append({'type': 'Feature',
     'properties': {'track_label': name[0], 'line_code': name[1], 'track_name': name[2], 'line_name': name[3]},
     'geometry': {
         'type': 'LineString',
         'coordinates': line,
     }})

We plot the map:

In [8]:
lines_geojson = {'type': 'FeatureCollection', 'features': lines_geojson_features}
map_ = folium.Map([48.8566, 2.3522], tiles='cartodbpositron', zoom_start=5)
folium.GeoJson(lines_geojson,
               tooltip=folium.GeoJsonTooltip(fields=['track_label', 'track_name', 'line_code', 'line_name'],
                                             aliases=['Track label', 'Track name', 'Line code', 'Line name'])
              ).add_to(map_)
map_